#NetCDF4 features

#Read a NetCDF4 file with groups

## Import numpy and Nio

In [ ]:
import numpy
import Nio

## Open a NetCDF4 file, and print the file info

In [ ]:
file = Nio.open_file("../Data/nc4_withgroup.nc", "r")

print file

## Print the attributes

In [ ]:
print "file.attributes:"
print file.attributes

n = 0
for name in file.attributes.keys():
    print "Global attr %d %20s: %s" %(n, name, getattr(file, name))
    n += 1

## Print Dimensions

In [ ]:
print "file.dimensions:"
print file.dimensions

n = 0
for name in file.dimensions.keys():
    print "Dim %2.2d name: %6s, size: %4d" %(n, name, file.dimensions[name])
    n += 1

## Print Variables info

In [ ]:
print "file.variables:"
print file.variables

n = 0
for name in file.variables.keys():
    print "Var %d: <%s>" %(n, name)
    n += 1

## Print Groups info

In [ ]:
print "file.groups:"
print file.groups

n = 0
for name in file.groups.keys():
    print "Group %d: <%s>" %(n, name)
    n += 1

## Get group "forecast" from file

In [ ]:
forecasts = file.groups['forecasts']

print "forecasts:\n"
print forecasts

## Get group "model1" from group forecast

In [ ]:
mdl_one = forecasts.groups['model1']

print "mdl_one:\n"
print mdl_one

## Get variable from model1

In [ ]:
temp = mdl_one.variables['temp']

## Show temp's attributes

In [ ]:
n = 0
for name in temp.attributes.keys():
    print "temp attr %d %20s: %s" %(n, name, temp.attributes[name])
    n += 1

## Check temp's other info

In [ ]:
print "temp type: ", temp.typecode()
numDims = temp.rank
print "numDims = ", numDims
dimSizes = temp.shape
dimNames = temp.dimensions
n = 0
while(n < numDims):
    print "Dim %2d name: %6s, size: %4d" %(n, dimNames[n], dimSizes[n])
    n += 1

## Show temp's value

In [ ]:
print "temp value:", temp

## Close the file

In [ ]:
file.close()

# Read string variable from a file

In [ ]:
fn = "../Data/strings.nc"
file = Nio.open_file(fn, mode="r")

print "file <%s>:" %(fn)
print file

strs = file.variables['universal_declaration_of_human_rights'][:]

print "strs:"
print  strs

file.close()

#Write a string variable to file

##Read a string variable first

In [ ]:
fn = "../Data/strings.nc"
file = Nio.open_file(fn, mode="r")

print "file <%s>:" %(fn)
print file

varname = 'universal_declaration_of_human_rights'
strs = file.variables[varname].get_value()

print "strs:"
print  strs

file.close()

##write to file

In [ ]:
import os, time

opt = Nio.options()
opt.Format = 'NetCDF4'

print opt.Format

#create a file
fatt = "Created at " + time.ctime(time.time())
fn = "pynio_strings.nc"
if(os.path.isfile(fn)):
    os.remove(fn)

strf = Nio.open_file(fn, options=opt, history=fatt, mode="w")
strf.source   = "Nio created NetCDF4 string variable"
strf.history = "Created " + time.ctime(time.time())

print "len(strs) = ", len(strs)

nstrings = strf.create_dimension('nstrings', len(strs))

newstrs = strf.create_variable("newstrs", "S1", ("nstrings", ))

newstrs[:] = strs[:]

strf.close()

# Read vlen variable

In [ ]:
fn = "../Data/vlen.nc"
file = Nio.open_file(fn, "r")

print "file:"
print file

var = file.variables['vlen_var'][:]

print "var:"
print var

file.close()

# Write vlen variable

In [ ]:
opt = Nio.options()
opt.Format = 'NetCDF4'

print opt.Format

#create a file
hatt = "Created at " + time.ctime(time.time())
fn = "pynio_vlen.nc"
if(os.path.isfile(fn)):
    os.remove(fn)
file = Nio.open_file(fn, options=opt, history=hatt, mode="w")

#create global attributes
file.source   = "Nio created NetCDF4 vlen file"
file.history = "Created " + time.ctime(time.time())

nx = 3
ny = 4

x = file.create_dimension('x', nx)
y = file.create_dimension('y', ny)

print "file after add dimensions:"
print file

data = numpy.empty(ny*nx, object)
m = 0
for n in range(ny*nx):
    m += 1
    data[n] = numpy.arange(m, dtype='int32')+1
data = numpy.reshape(data,(ny, nx))

print "data", data

vlvar = file.create_vlen('vlen_var', 'i', ('y','x'))
vlvar[:] = data

file.close()

# Read compound data

In [ ]:
fn = "../Data/compound.nc"
file = Nio.open_file(fn, mode="r")

print "file <%s>:" %(fn)
print file

station_data = file.variables['station_data'][:]

print "station_data:"
print  station_data

file.close()

#Write compound data

In [ ]:
opt = Nio.options()
opt.Format = 'NetCDF4'

print opt.Format

#create a file
hatt = "Created at " + time.ctime(time.time())
fn = "pynio_compound.nc"
if(os.path.isfile(fn)):
    os.remove(fn)
file = Nio.open_file(fn, options=opt, history=hatt, mode="w")

#create global attributes
file.source   = "Nio created NetCDF4 compound variable"
file.history = "Created " + time.ctime(time.time())

print "file after add attributes:"
print file

#create an unlimited  dimension call 'station'
station = file.create_dimension('station', None)
nstations = 10

print "station:"
print  station

print "nstations:"
print  nstations

#define a compound data type (can contain arrays, or nested compound types).
NUMCHARS = 80 # number of characters to use in fixed-length strings.
station_datatype = numpy.array([['latitude', 'f'],
                                ['longitude', 'f'],
                                ['location_name', 'S1', NUMCHARS],
                                ['speed', 'f'],
                                ['direction', 'i'],
                                ['temp_sounding', 'f', 10],
                                ['press_sounding', 'i', 10]])

print "len(station_datatype) = ", len(station_datatype)
print "station_datatype:"
print  station_datatype

#now that station_datatype is defined, create the station data type.
station_data = file.create_compound('station_data', station_datatype, ('station',))

#create a numpy structured array, assign data to it.
data = {}
data['latitude'] = 40.
data['longitude'] = -105.
data['location_name'] = "Boulder, Colorado, USA'"
data['speed'] = 12.5
data['direction'] = 270
data['temp_sounding'] = [280.3,272.,270.,269.,266.,258.,254.1,250.,245.5,240.]
data['press_sounding'] = range(800,300,-50)

station = numpy.empty(2, object)

#assign structured array to variable slice.
#station[0] = data

#or just assign a tuple of values to variable slice
#(will automatically be converted to a structured array).
station[0] = [[40.],[-105.],
              ["Boulder, Colorado, USA"],
              [12.5],[270],
              [280.3,272.,270.,269.,266.,258.,254.1,250.,245.5,240.],
              range(800,300,-50)]
station[1] = [[40.78],[-73.99],
              ["New York, New York, USA"],
              [-12.5],[90],
              [290.2,282.5,279.,277.9,276.,266.,264.1,260.,255.5,243.],
              range(900,400,-50)]

station_data[:] = station

file.close()

#Walk through groups in NetCDF4 file

In [ ]:
def walktree(top):
     values = top.groups.values()
     yield values
     for value in top.groups.values():
         for children in walktree(value):
             yield children
import Nio
f = Nio.open_file("../Data/nc4_withgroup.nc") 

print "all groups in the file:"
print f.groups
print "\n\ntraversing the group tree:"
rgroup = f.groups['/']
#print "root group:", repr( rgroup)
print "root group: %s contains %d groups, %d variables" \
      %(rgroup.name, len(rgroup.groups), len(rgroup.variables))
print "\t\t%d dimensions, and %d group-attributes.\n" \
      %(len(rgroup.dimensions), len(rgroup.attributes))
for children in walktree(f.groups['/']):
   #if len(children) > 0:
   #    print "\tgroups:", children
    for child in children:
       #print child
        print "\tgroup: %s contains %d groups, %d variables" \
              %(child.name, len(child.groups), len(child.variables))
        print "\t\t\t%d dimensions, and %d group-attributes.\n" \
              %(len(child.dimensions), len(child.attributes))

#Create groups in a file

In [ ]:
opt = Nio.options()
opt.Format = 'NetCDF4'

print opt.Format

#create a file
hatt = "Created at " + time.ctime(time.time())
fn = "pynio_created_nc4_withgroup.nc"
if(os.path.isfile(fn)):
    os.remove(fn)
file = Nio.open_file(fn, options=opt, history=hatt, mode="w")

#create global attributes
file.source   = "Nio created NetCDF4 file"
file.history = "Created " + time.ctime(time.time())

#Create some groups.
forecast = file.create_group("forecast")
analysis = file.create_group("analysis")

fmdl1 = forecast.create_group("model1")
fmdl2 = forecast.create_group("model2")
amdl1 = analysis.create_group("model1")
amdl2 = analysis.create_group("model2")

ntimes = 5
nlevels = 10
nlats = 73
nlons = 144

#Create some dimensions.
fmdl1.create_dimension("time", None)
fmdl1.create_dimension("level", None)
fmdl1.create_dimension("lat", nlats)
fmdl1.create_dimension("lon", nlons)

mtimes = 1
mlevels = (nlevels+1)/2
mlats = (nlats+1)/2
mlons = (nlons+1)/2

#Create chunk dimensions.
fmdl1.create_chunk_dimension("time", mtimes)
fmdl1.create_chunk_dimension("level", mlevels)
fmdl1.create_chunk_dimension("lat", mlats)
fmdl1.create_chunk_dimension("lon", mlons)

#Create variables.
time  = fmdl1.create_variable("time",  "d", ("time",))
level = fmdl1.create_variable("level", "i", ("level",))
lat   = fmdl1.create_variable("lat",   "f", ("lat",))
lon   = fmdl1.create_variable("lon",   "f", ("lon",))
temp  = fmdl1.create_variable("temp" , "f", ("time", "level", "lat", "lon"))

#Specify attributes.
time.units = "hours since 0001-01-01 00:00:00.0"
time.calendar = "gregorian"
level.units = "hPa"
lat.units = "degrees north"
lon.units = "degrees east"
temp.units = "K"

#fill in variables.
time[:] = [0.0, 12.0, 24.0, 36.0, 48.0]
level[:] =  [1000, 850, 700, 500, 300, 250, 200, 150, 100, 50]
latvalues = numpy.arange(-90, 91, 2.5, 'float32')
lonvalues = numpy.arange(-180, 180, 2.5, 'float32')

tshape = time.shape
lshape = level.shape
print('time shape = ', tshape[0])
print('level shape = ', lshape[0])

from numpy.random.mtrand import uniform # random number generator.
tempvalues = uniform(200.0, 300.0, size=(ntimes, nlevels, nlats, nlons))
ftempvalues = numpy.ndarray(shape=(ntimes, nlevels, nlats, nlons), dtype=numpy.float32)

ftempvalues[:,:,:,:] = tempvalues[:,:,:,:]
lat[:] = latvalues
lon[:] = lonvalues
temp[:] = ftempvalues

#Write other variables to file

In [ ]:
#test data types
nx = 2
#Create dimension.
amdl1.create_dimension("x", nx)

#Create some variables.
vdbl = amdl1.create_variable("vdbl", "d", ("x",))
vdbl[:] = numpy.array([0.1234456789, 1.2345678901], numpy.double)

vflt = amdl1.create_variable("vflt", "f", ("x",))
vflt[:] = [0.1234456, 1.234567]

vint64 = amdl1.create_variable("vint64", "q", ("x",))
vint64[:] = numpy.array([-12344567890, 12345678901234], numpy.int64)

vuint64 = amdl1.create_variable("vuint64", "Q", ("x",))
vuint64[:] = numpy.array([1234456789, 1234567890123], numpy.uint64)

vlong = amdl1.create_variable("vlong", "l", ("x",))
vlong[:] = numpy.array([-1234567, 7654321], numpy.int64)

vulong = amdl1.create_variable("vulong", "L", ("x",))
vulong[:] = numpy.array([1234567, 87654321], numpy.uint64)

vint = amdl1.create_variable("vint", "i", ("x",))
vint[:] = numpy.array([-1234456, 1234567], numpy.int32)

vuint = amdl1.create_variable("vuint", "I", ("x",))
vuint[:] = numpy.array([1234456, 234567], numpy.uint32)

vshort = amdl1.create_variable("vshort", "h", ("x",))
vshort[:] = numpy.array([-12345, 12345], numpy.int16)

vushort = amdl1.create_variable("vushort", "H", ("x",))
vushort[:] = numpy.array([12345, 23451], numpy.uint16)

vbyte = amdl1.create_variable("vbyte", "b", ("x",))
vbyte[:] = numpy.array([-123, 123], numpy.int8)

vubyte = amdl1.create_variable("vubyte", "B", ("x",))
vubyte[:] = numpy.array([123, 234], numpy.uint8)

#vchar = amdl1.create_variable("vchar", "c", ("x",))
#vchar[:] = numpy.chararray([23, 123], numpy.chararray)
#amdl1.variables['vchar'][:] = vchar

vlogical = amdl1.create_variable("vlogical", "?", ("x",))
vlogical[:] = [0, 1]

vstring = amdl1.create_variable("vstring", "S1", ("x",))
vstring[:] = ["abcdef", "XYZ"]

file.close()